<a href="https://colab.research.google.com/github/SumitP31/MARL/blob/main/test.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [210]:
import numpy as np
import random

walls =[(0,0),(0,1),(0,2),(0,3),(0,4),(0,5),(0,6),

(1,0),(1,6),

(2,0),(2,6),

(3,0),(3,1),(3,4),(3,5),(3,6),

(4,0), (4,1), (4,4),(4,5),(4,6),

(5,0), (5,1), (5,2), (5,3), (5,4), (5,5), (5,6)]


goal = (1,3)

box_pose = (3,2)

start = (2,1)

actions = ('up', 'down', 'left', 'right')

grid_sz = (6, 7)

In [211]:
states = []

for i in range(grid_sz[0]):
    for j in range(grid_sz[1]):
        if (i,j) not in walls:
            states.append((i,j))

print(states)

[(1, 1), (1, 2), (1, 3), (1, 4), (1, 5), (2, 1), (2, 2), (2, 3), (2, 4), (2, 5), (3, 2), (3, 3), (4, 2), (4, 3)]


In [212]:
policy = {}
for s in states:
    policy[s] = random.choice(actions)
print(policy)

{(1, 1): 'up', (1, 2): 'up', (1, 3): 'right', (1, 4): 'down', (1, 5): 'right', (2, 1): 'right', (2, 2): 'down', (2, 3): 'right', (2, 4): 'up', (2, 5): 'left', (3, 2): 'down', (3, 3): 'right', (4, 2): 'right', (4, 3): 'right'}


In [213]:
rewards = np.zeros(grid_sz)
for s in states:
  rewards[s] = 0
for w in walls:
  rewards[w] = -100
rewards[goal] = 1000
print(rewards)

[[-100. -100. -100. -100. -100. -100. -100.]
 [-100.    0.    0. 1000.    0.    0. -100.]
 [-100.    0.    0.    0.    0.    0. -100.]
 [-100. -100.    0.    0. -100. -100. -100.]
 [-100. -100.    0.    0. -100. -100. -100.]
 [-100. -100. -100. -100. -100. -100. -100.]]


In [214]:
def generate_episode(start_state, start_action, walls, policy):
  episode = []
  state =start_state
  action = start_action
  ep_len = 50
  i=0
  while True:
    next_state, box_next = transition(state,action,walls,box_pose)
    reward = rewards[next_state]
    episode.append((state,action,reward))
    if box_next==goal or i>= ep_len:
      break
    state = next_state
    action = policy[state]
    i+=1
  return episode


In [215]:
def box_state(box_pose,walls,action):
    bx = box_pose[0]

    by = box_pose[1]


    if action == 'up':
        by -= 1
        # print(bx,by)
    if action == 'down':
        by += 1
        # print(bx,by)
    if action == 'left':
        bx -= 1

    if action == 'right':
        bx += 1

    new_box_pose = (bx, by)

    if new_box_pose in walls:
        return False

    return True

In [216]:
def transition(state, action, walls, box_pose):
    x = state[0]
    y = state[1]

    bx = box_pose[0]
    by = box_pose[1]

    collision = False
    move = False

    if action == 'up':
        y += 1
        if box_state((bx,by), walls, 'up'):
            if (x,y) == (bx,by):
                by += 1
                move = True

    elif action =='down':
         y -= 1
         if box_state((bx,by), walls, 'down'):


            if (x,y) == (bx,by):
                by -= 1
                move = True

    elif action == 'left':
        x -= 1
        if box_state((bx,by), walls, 'left'):

            if (x,y) == (bx,by):
              # print('yes')
              bx -= 1
              move = True

    elif action == 'right':
        x += 1
        if box_state((bx,by), walls, 'right'):
            if (x,y) == (bx,by):
                bx += 1
                move = True

    next_state = (x, y)
    next_box_pose = (bx, by)
    # print(next_state)
    # print(next_box_pose)

    if next_state in walls:
        next_state = state
        collision = True
    if next_box_pose in walls:
      next_box_pose = box_pose
      next_state = state
      collison = True

    # print(next_state)
    # print(next_box_pose)

    return next_state, next_box_pose, collision, move

print(transition((1,1),"up",walls,box_pose))

((1, 2), (3, 2), False, False)


In [217]:
import random
from collections import defaultdict

# actions = [0,1,2,3]
# val = np.array(grid_sz)
# for s in states:
#   value[s] = np.random.choice(actions)
val = np.zeros(grid_sz)

Q_value = defaultdict(lambda: defaultdict(float))  # Q(s,a) initially set to 0
for s in states:
    for a in actions:
        Q_value[s][a] = np.random.random()
# Q[s][a]

Returns = defaultdict(lambda: defaultdict(list))
# returns[s][a]

def MC(goal, box_pose, actions, walls, states, val, policy, Q_value, Returns, n_ep = 100, ep_len=10, gamma = 0.9):
  poli = policy
  Q = Q_value
  returns = Returns
  value = val
  for j in range(100):
      print(f"Running {j} episode--------------------------------")
      b_p = box_pose
      # episode = generate_episode
      # s = random.choice(states)
      # a = random.choice(actions)

      for s in states:
        for a in actions:
          episode = []
          i =0
          action = a
          state = s
          while i<= ep_len :
            s_next, box_next , collision, move = transition(state,action,walls,b_p)
            if collision:
              reward = -1
            elif move:
              reward = 1
            else:
              reward = rewards[box_next]
            print(reward)
            episode.append((b_p,state,action,reward))
            if reward == 1000:
              break
            b_p = box_next
            action = poli[s_next]
            print(action)
            state = s_next
            i+=1

          print(episode)
          G = 0
          visited = set()
          for t in reversed(range(len(episode))):
            box_state, state, action, reward = episode[t]
            G = gamma*G + reward
            if (state,action) not in visited:
              visited.add((state, action))
              returns[state][action].append(G)
              Q[state][action] = np.mean(returns[state][action])
              # print("----------------")
              # print(Q[state], key=Q[state].get)
              # print("----------------")
              poli[state] = max(Q[state], key=Q[state].get)
  return poli , Q






In [218]:
policy , Q_value = MC(goal,box_pose, actions, walls, states, values, policy, Q_value, Returns)
print(policy)

Running 0 episode--------------------------------
0.0
up
0.0
right
0.0
right
0.0
right
0.0
right
-1
right
-1
right
-1
right
-1
right
-1
right
-1
right
[((3, 2), (1, 1), 'up', 0.0), ((3, 2), (1, 2), 'up', 0.0), ((3, 2), (1, 3), 'right', 0.0), ((3, 2), (2, 3), 'right', 0.0), ((3, 2), (3, 3), 'right', 0.0), ((3, 2), (4, 3), 'right', -1), ((3, 2), (4, 3), 'right', -1), ((3, 2), (4, 3), 'right', -1), ((3, 2), (4, 3), 'right', -1), ((3, 2), (4, 3), 'right', -1), ((3, 2), (4, 3), 'right', -1)]
-1
down
-1
down
-1
down
-1
down
-1
down
-1
down
-1
down
-1
down
-1
down
-1
down
-1
down
[((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1), ((3, 2), (1, 1), 'down', -1)]
-1
right
0.0
right
-1
right
-1
right
-1
right
-1
right
-1
right
-1
right
-1
right
-1
righ

In [219]:
# def Monte_Carlo(start, goal, box_pose, actions, walls, states, values, policy, n_episode = 10,episode_len = 20, gamma = 1):
#   Q = np.zeros((grid_sz[0],grid_sz[1],len(actions)))
#   poli =policy
#   N = np.zeros((grid_sz[0],grid_sz[1],len(actions)))
#   total_steps = []
#   for i in range(n_episode):
#     state = start
#     episode = []
#     steps = 0
#     while steps<episode_len:
#       action = np.random.choice(actions)
#       next_state, box_next = transition(state, action, walls, box_pose)
#       reward = rewards[next_state]
#       episode.append((state,action,reward))
#       state = next_state
#       box_pose = box_next
#       steps += 1
#     total_steps.append(steps)

#     returns = 0
#     for j in range(len(episode)-1, -1, -1):
#       state, action, reward = episode[j]
#       returns = gamma*returns + reward
#       act = actions.index(action)
#       N[s][act] += 1
#       Q[s][act] += (returns - Q[s][act])/N[s][act]
#     print(i)
#     policy = np.argmax(Q, axis=1)

#   return policy, Q




In [220]:
# action = 'up'
# N = np.zeros((grid_sz[0],grid_sz[1],4))
# s = (3,3)
# N[s][actions.index(action)] = 1
# print(N)